In [35]:
import numpy as np
import pandas as pd
import seaborn as sns
import matplotlib.pyplot as plt

from sklearn.metrics import (
    accuracy_score,
    f1_score,
    classification_report,
    confusion_matrix,
    roc_auc_score,
)

In [36]:
df = pd.read_csv("../our_analyses/dataset_prepared.csv")

In [37]:
from sklearn.preprocessing import LabelEncoder

df=df.drop(['name', 'artists', 'album_name'], axis=1)

# genre_groups = {
#     'j-dance': 0, 'techno': 0, 'mandopop': 0, 'idm': 0, 'chicago-house': 0, 'breakbeat': 0,  # Elettronica/Dance
#     'black-metal': 1,  # Metal/Rock
#     'bluegrass': 2,  # Country/Folk
#     'j-idol': 3, 'spanish': 3, 'disney': 3, 'brazil': 3,  # Pop/Commerciale
#     'iranian': 4, 'afrobeat': 4, 'indian': 4, 'forro': 4,  # World
#     'happy': 5, 'sleep': 5, 'study': 5,  # Ambient/New Age
#     'industrial': 6  # Other
# }
genre_groups = {
    'j-dance': 0, 'techno': 0, 'chicago-house': 0, 'breakbeat': 0, 
        'happy': 1, 'sleep': 1, 'study': 1, 'disney': 1, 
        'bluegrass': 2, 'forro': 2, 'mandopop': 2, 'iranian': 2, 'indian': 2, 'brazil': 2, 
        'black-metal': 3, 'industrial': 3, 
        'j-idol': 4, 'spanish': 4, 'afrobeat': 4, 
        'idm': 5
}
genre_labels = ['Metal and Related', 'Metal/Rock', 'Country/Folk', 'Pop/Commercial', 'World', 'Ambient/New Age', 'Other', 'Indian']


# Mappatura dei generi del dataframe ai gruppi di generi
df['genre_group'] = df['genre'].map(genre_groups).astype(int)

# Stampa del mapping dei generi ai numeri corrispondenti
print(df['genre_group'].unique())

le = LabelEncoder()
df['explicit'] = le.fit_transform(df['explicit'])

df = df.drop('genre', axis=1)

[4 3 2 0 1 5]


In [38]:
df.head()

duration_ms  explicit  popularity  danceability  energy  key  loudness  \
0       293106         0          50         0.401   0.683    8    -5.722   
1       194972         0          52         0.672   0.858    3    -5.233   
2       178428         0          22         0.636   0.826    3    -7.486   
3       238373         0          20         0.733   0.862    7    -5.813   
4       221893         0          22         0.712   0.225    5   -10.017   

   mode  speechiness  acousticness  instrumentalness  liveness  valence  \
0     1       0.0401         0.181          0.000000    0.0837    0.226   
1     1       0.1450         0.456          0.811000    0.1040    0.963   
2     1       0.0585         0.461          0.271000    0.1410    0.731   
3     1       0.0604         0.287          0.000532    0.4660    0.745   
4     1       0.0533         0.930          0.001000    0.1230    0.429   

     tempo  time_signature  genre_group  
0  135.951             4.0            4  
1  166.689             4.0            4  
2  102.809             4.0            4  
3  107.981             4.0            4  
4   87.520             4.0            4

In [39]:
from sklearn.model_selection import train_test_split

attributes = [col for col in df.columns if col != 'genre_group']
X = df[attributes].values
y = df['genre_group']

X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.3, random_state=1, stratify=y) # we use 70% and 30% and we stratisfy to have the same distribution for the classes between them in the training and in the test set

In [48]:
X

array([[2.93106e+05, 0.00000e+00, 5.00000e+01, ..., 2.26000e-01,
        1.35951e+02, 4.00000e+00],
       [1.94972e+05, 0.00000e+00, 5.20000e+01, ..., 9.63000e-01,
        1.66689e+02, 4.00000e+00],
       [1.78428e+05, 0.00000e+00, 2.20000e+01, ..., 7.31000e-01,
        1.02809e+02, 4.00000e+00],
       ...,
       [2.34005e+05, 0.00000e+00, 5.40000e+01, ..., 5.29000e-01,
        1.19991e+02, 4.00000e+00],
       [2.61093e+05, 0.00000e+00, 5.60000e+01, ..., 9.07000e-01,
        1.30009e+02, 4.00000e+00],
       [3.08466e+05, 0.00000e+00, 4.30000e+01, ..., 3.22000e-02,
        1.23009e+02, 4.00000e+00]])

In [40]:
from sklearn.tree import DecisionTreeClassifier, plot_tree

In [41]:
dt = DecisionTreeClassifier()

dt.fit(X_train, y_train)

DecisionTreeClassifier()

In [42]:
y_train_pred = dt.predict(X_train)
y_test_pred = dt.predict(X_test)

In [43]:
print('Train Accuracy %s' % accuracy_score(y_train, y_train_pred))
print('Train F1-score %s' % f1_score(y_train, y_train_pred, average=None))
print()

print('Test Accuracy %s' % accuracy_score(y_test, y_test_pred))
print('Test F1-score %s' % f1_score(y_test, y_test_pred, average=None))

Train Accuracy 1.0
Train F1-score [1. 1. 1. 1. 1. 1.]

Test Accuracy 0.5637777777777778
Test F1-score [0.56333333 0.60142936 0.67233099 0.56064073 0.38772455 0.29741379]


In [51]:
plt.figure(figsize=(50, 30), dpi=300)
plot_tree(dt, feature_names=attributes, filled=True)
plt.show()

In [45]:
print(classification_report(y_test, y_test_pred))

              precision    recall  f1-score   support

           0       0.56      0.56      0.56       900
           1       0.60      0.61      0.60       900
           2       0.67      0.67      0.67      1350
           3       0.58      0.54      0.56       450
           4       0.39      0.38      0.39       675
           5       0.29      0.31      0.30       225

    accuracy                           0.56      4500
   macro avg       0.51      0.51      0.51      4500
weighted avg       0.56      0.56      0.56      4500



In [46]:
import plotly.figure_factory as ff
from sklearn.metrics import confusion_matrix

# Assumiamo che 'y_test' e 'y_test_pred' siano già definiti e contengano le etichette vere e predette dal tuo modello

# Genera la matrice di confusione
cf = confusion_matrix(y_test, y_test_pred)

# Definisci le etichette per i generi in base ai raggruppamenti definiti
genre_labels = ['Dance/Electronic', 'Ambient/Relaxing', 'Global/Traditional', 'Metal/Industrial', 'Pop/World', 'Experimental/Electronic']

# Crea la heatmap usando plotly
fig = ff.create_annotated_heatmap(z=cf, x=genre_labels, y=genre_labels,
                                  annotation_text=cf.astype(str), colorscale='Greens')

# Aggiorna il layout
fig.update_layout(title_text='Confusion Matrix', title_x=0.5,
                  xaxis=dict(title='Predicted Labels', tickangle=45),
                  yaxis=dict(title='True Labels', tickmode='array', tickvals=list(range(len(genre_labels))), ticktext=genre_labels),
                  yaxis_autorange='reversed')  # Reverse the y-axis to have the first class at the top

# Mostra il grafico
fig.show()


In [49]:
zipped = zip(attributes, dt.feature_importances_)
zipped = sorted(zipped, key=lambda x: x[1], reverse=True)
for col, imp in zipped:
    print(col, imp)

acousticness 0.13711748065111026
popularity 0.12643116409283703
duration_ms 0.11442363745115522
danceability 0.1097287424503168
instrumentalness 0.10402286561364305
valence 0.07210793168617217
speechiness 0.06955065970221208
loudness 0.06320680919664831
energy 0.06172358637342185
tempo 0.056154342417696394
liveness 0.04438078794864583
key 0.02232044370872195
explicit 0.009677282833224134
mode 0.005116214635406621
time_signature 0.0040380512387881515
